In [1]:
import pandas as pd
from sklearn import datasets
    
from evidently import Dataset
from evidently import DataDefinition
from evidently import Report
from evidently.presets import DataDriftPreset, DataSummaryPreset 

In [11]:
titanic_data = datasets.fetch_openml(name="titanic", version = 1, as_frame="auto")
titanic = titanic_data.frame

titanic.head()

pclass survived                                             name     sex  \
0       1        1                    Allen, Miss. Elisabeth Walton  female   
1       1        1                   Allison, Master. Hudson Trevor    male   
2       1        0                     Allison, Miss. Helen Loraine  female   
3       1        0             Allison, Mr. Hudson Joshua Creighton    male   
4       1        0  Allison, Mrs. Hudson J C (Bessie Waldo Daniels)  female   

       age  sibsp  parch  ticket      fare    cabin embarked boat   body  \
0  29.0000      0      0   24160  211.3375       B5        S    2    NaN   
1   0.9167      1      2  113781  151.5500  C22 C26        S   11    NaN   
2   2.0000      1      2  113781  151.5500  C22 C26        S  NaN    NaN   
3  30.0000      1      2  113781  151.5500  C22 C26        S  NaN  135.0   
4  25.0000      1      2  113781  151.5500  C22 C26        S  NaN    NaN   

                         home.dest  
0                     St Louis, MO  
1  Montreal, PQ / Chesterville, ON  
2  Montreal, PQ / Chesterville, ON  
3  Montreal, PQ / Chesterville, ON  
4  Montreal, PQ / Chesterville, ON

In [20]:
titanic["embarked"].value_counts()

embarked
S    914
C    270
Q    123
Name: count, dtype: int64

In [17]:
# leave only reasonable columns
titanic = titanic.drop(['name', 'ticket'], axis=1)


In [18]:
# create artificial split between reference and current dataset
titanic_ref = titanic[titanic["embarked"]!="Q"]
titanic_prod = titanic[titanic["embarked"]=="Q"]

In [25]:
schema = DataDefinition(
    numerical_columns=["age", "sibsp", "parch", "body"],
    categorical_columns=["pclass", "survived", "sex", "cabin", "embarked", "boat", "home.dest"],
    )

In [26]:
eval_data_1 = Dataset.from_pandas(
    pd.DataFrame(titanic_prod),
    data_definition=schema
)

In [27]:
eval_data_2 = Dataset.from_pandas(
    pd.DataFrame(titanic_ref),
    data_definition=schema
)

In [ ]:
report = Report([
    DataDriftPreset() 
])

my_eval = report.run(eval_data_1, eval_data_2)

c:\Users\User\Desktop\training\Evidently\.venv\lib\site-packages\scipy\stats\_stats_py.py:7335: RuntimeWarning: divide by zero encountered in divide
  terms = (f_obs - f_exp)**2 / f_exp
c:\Users\User\Desktop\training\Evidently\.venv\lib\site-packages\scipy\stats\_stats_py.py:7335: RuntimeWarning: divide by zero encountered in divide
  terms = (f_obs - f_exp)**2 / f_exp
c:\Users\User\Desktop\training\Evidently\.venv\lib\site-packages\scipy\stats\_stats_py.py:7335: RuntimeWarning: divide by zero encountered in divide
  terms = (f_obs - f_exp)**2 / f_exp
c:\Users\User\Desktop\training\Evidently\.venv\lib\site-packages\scipy\stats\_stats_py.py:7335: RuntimeWarning:

divide by zero encountered in divide

c:\Users\User\Desktop\training\Evidently\.venv\lib\site-packages\scipy\stats\_stats_py.py:7335: RuntimeWarning:

divide by zero encountered in divide

c:\Users\User\Desktop\training\Evidently\.venv\lib\site-packages\scipy\stats\_stats_py.py:7335: RuntimeWarning:

divide by zero encountered 

In [29]:
# run report
my_eval